In [1]:
import torch
import torchvision.models as models
import torchvision.transforms as transforms
from PIL import Image
import inspect

# 加载预训练的 VGG16 模型
model = models.vgg16(weights=models.VGG16_Weights.DEFAULT)
model.eval()  # 设置为评估模式

print("VGG16 文档:")
print(inspect.getdoc(models.vgg16))
print("\n" + "="*60 + "\n")

# 分析每一层的参数量
def analyze_vgg16_params(model):
    total_params = 0
    print(f"{'Layer Name':<20} {'Type':<15} {'Parameters':<12} {'Shape':<25} {'Description':<20}")
    print("-" * 100)
    
    # 分析特征提取部分 (卷积层)
    features_params = 0
    for i, layer in enumerate(model.features):
        if isinstance(layer, torch.nn.Conv2d):
            layer_params = sum(p.numel() for p in layer.parameters())
            features_params += layer_params
            total_params += layer_params
            print(f"{f'features[{i}]':<20} {'Conv2d':<15} {layer_params:<12} {str(tuple(layer.weight.shape)):<25} {f'卷积层 {i}'}")
        elif isinstance(layer, torch.nn.MaxPool2d):
            print(f"{f'features[{i}]':<20} {'MaxPool2d':<15} {'0':<12} {'-':<25} {'最大池化层'}")

    print(f"{'features_total':<20} {'-':<15} {features_params:<12} {'-':<25} {'特征提取部分总参数量'}")

    print("-" * 100)
    
    # 分析分类器部分 (全连接层)
    classifier_params = 0
    for i, layer in enumerate(model.classifier):
        if isinstance(layer, torch.nn.Linear):
            layer_params = sum(p.numel() for p in layer.parameters())
            classifier_params += layer_params
            total_params += layer_params
            if i == 0:
                desc = "第一个全连接层(4096)"
            elif i == 3:
                desc = "第二个全连接层(4096)"
            elif i == 6:
                desc = "分类层(1000类)"
            else:
                desc = "全连接层"
            print(f"{f'classifier[{i}]':<20} {'Linear':<15} {layer_params:<12} {str(tuple(layer.weight.shape)):<25} {desc}")
        elif isinstance(layer, torch.nn.Dropout):
            print(f"{f'classifier[{i}]':<20} {'Dropout':<15} {'0':<12} {'-':<25} {'Dropout层'}")
        elif isinstance(layer, torch.nn.ReLU):
            print(f"{f'classifier[{i}]':<20} {'ReLU':<15} {'0':<12} {'-':<25} {'激活函数'}")

    print(f"{'classifier_total':<20} {'-':<15} {classifier_params:<12} {'-':<25} {'分类器部分总参数量'}")

    print("-" * 100)
    print(f"{'TOTAL':<20} {'-':<15} {total_params:<12} {'-':<25} {'总参数量'}")
    
    return total_params

# 执行分析
total_params = analyze_vgg16_params(model)

print("\n" + "="*60)
print("VGG16 结构详细解释:")
print("="*60)

print("\n1. 网络结构概述:")
print("   - VGG16 包含 16 个带权重的层（13个卷积层 + 3个全连接层）")
print("   - 总参数量约为 138M")
print("   - 使用小尺寸3x3卷积核堆叠代替大卷积核")

print("\n2. 特征提取部分 (features):")
print("   - 包含13个卷积层和5个最大池化层")
print("   - 卷积层配置: 64-64-128-128-256-256-256-512-512-512-512-512-512")
print("   - 每经过一个池化层，特征图尺寸减半，通道数翻倍")
print("   - 所有卷积层都使用3x3卷积核，步长=1，填充=1")

print("\n3. 分类器部分 (classifier):")
print("   - 包含3个全连接层")
print("   - 第一全连接层: 25088 → 4096")
print("   - 第二全连接层: 4096 → 4096") 
print("   - 第三全连接层: 4096 → 1000 (分类输出)")
print("   - 全连接层参数量占总参数的约90%")

print("\n4. 参数量分布特点:")
print("   - 全连接层参数极其庞大（约1.2亿参数）")
print("   - 第一个全连接层就有约1亿参数")
print("   - 卷积层参数相对较少（约1.5千万参数）")

print("\n5. 与ResNet-18对比:")
print("   - VGG16参数量(138M) vs ResNet-18(11.7M): 约12倍")
print("   - VGG16层数更少但参数更多（主要在全连接层）")
print("   - ResNet使用全局平均池化大幅减少全连接参数")

print("\n6. 设计优缺点:")
print("   - 优点: 结构简单统一，性能优秀")
print("   - 缺点: 参数量巨大，计算成本高")
print("   - 改进: 后来的网络多用全局平均池化替代全连接层")

Downloading: "https://download.pytorch.org/models/vgg16-397923af.pth" to /root/.cache/torch/hub/checkpoints/vgg16-397923af.pth
100%|██████████| 528M/528M [01:51<00:00, 4.97MB/s] 


VGG16 文档:
VGG-16 from `Very Deep Convolutional Networks for Large-Scale Image Recognition <https://arxiv.org/abs/1409.1556>`__.

Args:
    weights (:class:`~torchvision.models.VGG16_Weights`, optional): The
        pretrained weights to use. See
        :class:`~torchvision.models.VGG16_Weights` below for
        more details, and possible values. By default, no pre-trained
        weights are used.
    progress (bool, optional): If True, displays a progress bar of the
        download to stderr. Default is True.
    **kwargs: parameters passed to the ``torchvision.models.vgg.VGG``
        base class. Please refer to the `source code
        <https://github.com/pytorch/vision/blob/main/torchvision/models/vgg.py>`_
        for more details about this class.

.. autoclass:: torchvision.models.VGG16_Weights
    :members:


Layer Name           Type            Parameters   Shape                     Description         
-----------------------------------------------------------------------